# Implementacion del modelo Rostlab/prot_xlnet para la generación de secuencias de aminoácidos

In [1]:
# ===================================================================
#  IMPORTACIÓN DE LIBRERÍAS
# ===================================================================
import os
import sys
import torch
import numpy as np
import pandas as pd
from pathlib import Path

# Machine Learning y Transformers
from sklearn.model_selection import train_test_split
from transformers import (
    XLNetLMHeadModel,
    XLNetTokenizer,
    Trainer,
    TrainingArguments,
    DataCollatorForLanguageModeling
)
from datasets import Dataset

# Asegurarse de que W&B esté deshabilitado si no se usa
os.environ["WANDB_DISABLED"] = "true"

In [2]:
# ===================================================================
#  CONFIGURACIÓN DE RUTAS Y PARÁMETROS
# ===================================================================

# --- Rutas del Proyecto ---
project_root = Path.cwd().parent
sys.path.append(str(project_root))
from src.bio_utils import fasta_to_dataframe

# Directorios principales
data_dir = project_root / "data"
processed_data_dir = data_dir / "processed"
output_dir = project_root / "models" / "prot_xlnet_finetuned2"

# Archivos FASTA de entrada
fasta_file_cdhit = processed_data_dir / "cd-hit_results.fasta"
fasta_file_125 = processed_data_dir / "125_EC50.fasta"

# --- Hiperparámetros del Modelo ---
MODEL_NAME = "Rostlab/prot_xlnet"
BATCH_SIZE = 8
NUM_EPOCHS = 5
LEARNING_RATE = 5e-5
MAX_LENGTH = 128

# --- Dispositivo (GPU/CPU) ---
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Usando dispositivo: {device}")
print(f"El modelo afinado se guardará en: {output_dir}")

# Crear directorio de salida
output_dir.mkdir(parents=True, exist_ok=True)

Usando dispositivo: cuda
El modelo afinado se guardará en: d:\source\Proyecto Integrador\glp-1_drug_discovery\models\prot_xlnet_finetuned2


In [3]:
# ===================================================================
# CARGAR Y FORMATEAR DATOS
# ===================================================================
print("Cargando secuencias desde archivos FASTA...")
df_cd_hit = fasta_to_dataframe(fasta_file_cdhit)
df_glp1 = fasta_to_dataframe(fasta_file_125)

df_sequences = pd.concat([df_cd_hit, df_glp1], ignore_index=True)
df_sequences = df_sequences.drop_duplicates(subset=["sequence"]).reset_index(drop=True)
df_sequences = df_sequences[["sequence"]]

# Añadir espacios entre cada aminoácido para el tokenizador ProtXLNet
df_sequences['sequence'] = df_sequences['sequence'].apply(lambda x: ' '.join(list(x)))

print(f"Total de secuencias únicas cargadas y formateadas: {len(df_sequences)}")
print("\nVista previa de los datos formateados:")
print(df_sequences.head())

Cargando secuencias desde archivos FASTA...
Total de secuencias únicas cargadas y formateadas: 350

Vista previa de los datos formateados:
                                            sequence
0  H A E G T Y T S D M S S Y L Q D Q A A K E F V ...
1  H A E G T Y T S D V S S Y L Q D Q A A K E F V ...
2  H A D G T Y T S D V S T Y L Q D Q A A K D F V ...
3  H A E G T Y T S D I T S Y L E G Q A A K E F I ...
4  H A D G T F T S D V S S Y L K D Q A I K D F V ...


In [4]:
# ===================================================================
#  PRUEBA DE GENERACIÓN CON EL MODELO ORIGINAL
# ===================================================================
print("--- Realizando prueba de generación con el modelo PRE-ENTRENADO original ---")

tokenizer_base = XLNetTokenizer.from_pretrained(MODEL_NAME)
model_base = XLNetLMHeadModel.from_pretrained(MODEL_NAME)
model_base.to(device)
model_base.eval()

prompt = "C A E G F T S D A K E F I L V K R"
print(f"\nGenerando secuencias base con el prompt: '{prompt}'")
inputs = tokenizer_base(prompt, return_tensors="pt").to(device)

with torch.no_grad():
    base_outputs = model_base.generate(
        input_ids=inputs["input_ids"],
        attention_mask=inputs["attention_mask"], # Añadimos la máscara para evitar errores en el dispositivo
        max_length=34,
        num_return_sequences=5,
        do_sample=True,
        temperature=1.0,
        pad_token_id=tokenizer_base.eos_token_id
    )

print("\nSecuencias generadas por el modelo original:")
for i, output in enumerate(base_outputs):
    generated_text = tokenizer_base.decode(output, skip_special_tokens=True)
    print(f"Base {i+1}: {generated_text}")

--- Realizando prueba de generación con el modelo PRE-ENTRENADO original ---

Generando secuencias base con el prompt: 'C A E G F T S D A K E F I L V K R'


This is a friendly reminder - the current text generation call has exceeded the model's predefined maximum length (-1). Depending on the model, you may observe exceptions, performance degradation, or nothing at all.



Secuencias generadas por el modelo original:
Base 1: C A E G F T S D A K E F I L V K R H H H H H H H H H H H H H H Q
Base 2: C A E G F T S D A K E F I L V K R R Y Y Y Y Y Y Y Y Y Y Y Y F Y
Base 3: C A E G F T S D A K E F I L V K R V V V V V V V V V V V V V V V
Base 4: C A E G F T S D A K E F I L V K R K R K R R R R R R R R R R R R
Base 5: C A E G F T S D A K E F I L V K R H H H H H H L V V V V V V V V


In [5]:
# ===================================================================
# TOKENIZACIÓN PARA EL FINE-TUNING
# ===================================================================
print("\n--- Iniciando preparación para el fine-tuning ---")
tokenizer = XLNetTokenizer.from_pretrained(MODEL_NAME)

train_df, val_df = train_test_split(df_sequences, test_size=0.15, random_state=42)
train_dataset = Dataset.from_pandas(train_df)
val_dataset = Dataset.from_pandas(val_df)

def tokenize_function(examples):
    tokenized = tokenizer(examples["sequence"], padding="max_length", truncation=True, max_length=MAX_LENGTH)
    tokenized["labels"] = tokenized["input_ids"].copy()
    return tokenized

print("Tokenizando los datasets...")
train_dataset = train_dataset.map(tokenize_function, batched=True, remove_columns=["sequence", "__index_level_0__"])
val_dataset = val_dataset.map(tokenize_function, batched=True, remove_columns=["sequence", "__index_level_0__"])
print("Datasets tokenizados.")


--- Iniciando preparación para el fine-tuning ---
Tokenizando los datasets...


Map:   0%|          | 0/297 [00:00<?, ? examples/s]

Map:   0%|          | 0/53 [00:00<?, ? examples/s]

Datasets tokenizados.


In [6]:
# ===================================================================
# CONFIGURAR Y EJECUTAR EL ENTRENAMIENTO FINALE DEL MODELO ProtXLNet
# ===================================================================
from transformers import get_linear_schedule_with_warmup

model = XLNetLMHeadModel.from_pretrained(MODEL_NAME)
model.to(device)

# Congelamiento selectivo
for param in model.parameters(): param.requires_grad = False
for param in model.lm_loss.parameters(): param.requires_grad = True

# Descongelar las últimas capas del transformador
num_layers_to_unfreeze = 8 

for layer in model.transformer.layer[-num_layers_to_unfreeze:]:
    for param in layer.parameters(): param.requires_grad = True

data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm=False)

# ===================================================================

# Calculamos ambos conteos
total_params = sum(p.numel() for p in model.parameters())
trainable_params = sum(p.numel() for p in model.parameters() if p.requires_grad)

print(f"\n[INFO] Resumen de parámetros para Fine-Tuning:")
print(f"  - Parámetros totales:     {total_params:,}")
print(f"  - Parámetros ENTRENABLES: {trainable_params:,}")
print(f"  - Porcentaje entrenable:  {100 * trainable_params / total_params:.2f}%")

# ===================================================================

# 1. Tasa de aprendizaje REDUCIDA
LEARNING_RATE = 2e-5

training_args = TrainingArguments(
    output_dir=str(output_dir), num_train_epochs=NUM_EPOCHS,
    per_device_train_batch_size=BATCH_SIZE, per_device_eval_batch_size=BATCH_SIZE,
    learning_rate=LEARNING_RATE, weight_decay=0.01,
    logging_steps=20, eval_strategy="epoch", save_strategy="epoch",
    load_best_model_at_end=True, fp16=torch.cuda.is_available(), report_to="tensorboard"
)

# 2. Creamos el optimizador y el planificador (scheduler)
optimizer = torch.optim.AdamW(model.parameters(), lr=LEARNING_RATE)

num_training_steps = NUM_EPOCHS * len(train_dataset) // BATCH_SIZE

lr_scheduler = get_linear_schedule_with_warmup(
    optimizer, num_warmup_steps=100, num_training_steps=num_training_steps
)

# Pasamos el optimizador y el scheduler al Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    data_collator=data_collator,
    optimizers=(optimizer, lr_scheduler)
)

print("\nIniciando el fine-tuning (versión estable)")
trainer.train()

trainer.save_model(str(output_dir))
tokenizer.save_pretrained(str(output_dir))
print(f"\nFine-tuning completado. Modelo guardado en: {output_dir}")


[INFO] Resumen de parámetros para Fine-Tuning:
  - Parámetros totales:     409,413,669
  - Parámetros ENTRENABLES: 109,204,517
  - Porcentaje entrenable:  26.67%

Iniciando el fine-tuning (versión estable)


There were missing keys in the checkpoint model loaded: ['lm_loss.weight'].



Fine-tuning completado. Modelo guardado en: d:\source\Proyecto Integrador\glp-1_drug_discovery\models\prot_xlnet_finetuned2


In [8]:
# --- 1. Cargar nuestro modelo y tokenizador afinados ---
tokenizer_fine_tuned = XLNetTokenizer.from_pretrained(str(output_dir))
model_fine_tuned = XLNetLMHeadModel.from_pretrained(str(output_dir))
model_fine_tuned.to(device)

XLNetLMHeadModel(
  (transformer): XLNetModel(
    (word_embedding): Embedding(37, 1024)
    (layer): ModuleList(
      (0-29): 30 x XLNetLayer(
        (rel_attn): XLNetRelativeAttention(
          (layer_norm): LayerNorm((1024,), eps=1e-12, elementwise_affine=True)
          (dropout): Dropout(p=0.1, inplace=False)
        )
        (ff): XLNetFeedForward(
          (layer_norm): LayerNorm((1024,), eps=1e-12, elementwise_affine=True)
          (layer_1): Linear(in_features=1024, out_features=4096, bias=True)
          (layer_2): Linear(in_features=4096, out_features=1024, bias=True)
          (dropout): Dropout(p=0.1, inplace=False)
          (activation_function): ReLU()
        )
        (dropout): Dropout(p=0.1, inplace=False)
      )
    )
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (lm_loss): Linear(in_features=1024, out_features=37, bias=True)
)

In [38]:
# ===================================================================
# GENERACIÓN CON EL MODELO AFINADO
# ===================================================================
print("\n--- Realizando prueba de generación con el modelo AFINADO ---")


model_fine_tuned.eval()
prompt = "B A E G T S D A K E F I W L V K R"
# --- 2. Usar el mismo prompt para comparar ---
print(f"\nGenerando secuencias afinadas con el mismo prompt: '{prompt}'")


inputs = tokenizer_fine_tuned(prompt, return_tensors="pt").to(device)

k = 9
p = 0.9
repetition_penalty = 1.8

# --- 3. Generar secuencias ---
with torch.no_grad():
    fine_tuned_outputs = model_fine_tuned.generate(
        input_ids=inputs["input_ids"],
        attention_mask=inputs["attention_mask"],
        max_length=40,
        num_return_sequences=5,
        do_sample=True,
        temperature=1.0,
        pad_token_id=tokenizer_base.eos_token_id,
        top_k=k,
        top_p=p,
        repetition_penalty=repetition_penalty,
    )

# --- 4. Decodificar y mostrar los resultados ---
print("\nSecuencias generadas por el modelo AFINADO:")
for i, output in enumerate(fine_tuned_outputs):
    generated_text = tokenizer_fine_tuned.decode(output, skip_special_tokens=True)
    print(f"Afinada {i+1}: {generated_text}")

print("\n¡Comparación finalizada! Revisa las secuencias para ver el efecto del entrenamiento.")


--- Realizando prueba de generación con el modelo AFINADO ---

Generando secuencias afinadas con el mismo prompt: 'B A E G T S D A K E F I W L V K R'

Secuencias generadas por el modelo AFINADO:
Afinada 1: X A E G T S D A K E F I W L V K R H H H H H H H H H H H H H H H
Afinada 2: X A E G T S D A K E F I W L V K R H Y Y Y Y Y Y H H H H H H H H
Afinada 3: X A E G T S D A K E F I W L V K R C Y Y Y Y Y Y Y Y H H H H H H H
Afinada 4: X A E G T S D A K E F I W L V K R H H H H H H H H H H H H H H H H
Afinada 5: X A E G T S D A K E F I W L V K R H Y H H H H H H H H H H H H H

¡Comparación finalizada! Revisa las secuencias para ver el efecto del entrenamiento.


In [39]:
import random
import torch
from tqdm.auto import tqdm # Para una barra de progreso útil

# Lista de aminoácidos estándar para realizar las mutaciones
AMINO_ACIDS = list("ACDEFGHIKLMNPQRSTVWY")

def generate_peptide_variants(
    prompt_sequences: list,
    model,
    tokenizer,
    num_variants_per_seq: int = 5,
    min_length: int = 25,
    max_length: int = 50
) -> list:
    """
    Genera nuevas variantes de péptidos introduciendo mutaciones aleatorias en
    un conjunto de secuencias de entrada y usando el modelo para completarlas.

    Args:
        prompt_sequences (list): Una lista de secuencias de péptidos (sin espacios)
                                 para usar como base para las mutaciones.
        model: El modelo de lenguaje afinado (fine-tuned).
        tokenizer: El tokenizador correspondiente al modelo.
        num_variants_per_seq (int): Cuántas variantes generar por cada secuencia de entrada.
        min_length (int): La longitud mínima de las secuencias generadas.
        max_length (int): La longitud máxima de las secuencias generadas.

    Returns:
        list: Una lista de secuencias de péptidos únicas generadas (sin espacios).
    """
    # Poner el modelo en modo de evaluación
    model.eval()
    device = model.device
    
    # Usamos un set para guardar solo las variantes únicas
    unique_variants = set()

    print(f"Iniciando generación de variantes para {len(prompt_sequences)} secuencias base...")

    # Iterar sobre cada secuencia de entrada con una barra de progreso
    for base_seq in tqdm(prompt_sequences, desc="Procesando secuencias"):
        if not base_seq:
            continue

        # Generar el número deseado de variantes para esta secuencia
        for _ in range(num_variants_per_seq):
            # 1. Crear una mutación aleatoria
            seq_list = list(base_seq)
            mutation_index = random.randint(0, len(seq_list) - 1)
            original_aa = seq_list[mutation_index]
            
            # Elegir un nuevo aminoácido que sea diferente al original
            new_aa = random.choice([aa for aa in AMINO_ACIDS if aa != original_aa])
            seq_list[mutation_index] = new_aa
            mutated_seq = "".join(seq_list)

            # 2. Preparar el prompt para el modelo (con espacios)
            prompt = " ".join(list(mutated_seq))
            
            # Tokenizar el prompt mutado
            inputs = tokenizer(prompt, return_tensors="pt").to(device)

            # 3. Generar variantes usando el modelo
            with torch.no_grad():
                outputs = model.generate(
                    input_ids=inputs["input_ids"],
                    attention_mask=inputs["attention_mask"],
                    min_length=min_length,
                    max_length=max_length,
                    do_sample=True,
                    temperature=1.0, # Temperatura estándar para un buen balance
                    top_k=90,
                    top_p=0.95,
                    pad_token_id=tokenizer.eos_token_id,
                    num_return_sequences=1 # Generamos una por mutación
                )

            # 4. Decodificar, limpiar y guardar la nueva variante
            for output in outputs:
                # La salida del modelo ya tiene el formato de espacios
                generated_text = tokenizer.decode(output, skip_special_tokens=True)
                # Quitar los espacios para tener el formato FASTA estándar
                cleaned_variant = generated_text.replace(" ", "")
                unique_variants.add(cleaned_variant)

    print(f"\nGeneración completada. Se encontraron {len(unique_variants)} variantes únicas.")
    return list(unique_variants)

In [40]:
def generate_peptide_variants_fast(
    prompt_sequences: list,
    model,
    tokenizer,
    num_variants_per_seq: int = 5,
    min_length: int = 25,
    max_length: int = 50,
    temperature: float = 1.0,
    top_k: int = 3,
    top_p: float = 0.95,
    batch_size: int = 32
) -> list:
    model.eval()
    device = model.device
    unique_variants = set()

    # --- Pre-generar todas las mutaciones ---
    mutated_prompts = []
    for base_seq in prompt_sequences:
        if not base_seq:
            continue
        for _ in range(num_variants_per_seq):
            seq_list = list(base_seq)
            idx = random.randrange(len(seq_list))
            aa = seq_list[idx]
            seq_list[idx] = random.choice([x for x in AMINO_ACIDS if x != aa])
            mutated_prompts.append(" ".join(seq_list))

    print(f"Generando {len(mutated_prompts)} variantes en lotes de {batch_size}...")

    # --- Procesar en lotes ---
    for i in tqdm(range(0, len(mutated_prompts), batch_size), desc="Generando"):
        batch_prompts = mutated_prompts[i:i + batch_size]
        inputs = tokenizer(batch_prompts, return_tensors="pt", padding=True, truncation=True).to(device)

        with torch.no_grad():
            outputs = model.generate(
                input_ids=inputs["input_ids"],
                attention_mask=inputs["attention_mask"],
                min_length=min_length,
                max_length=max_length,
                do_sample=True,
                temperature=temperature,
                top_k=top_k,
                top_p=top_p,
                pad_token_id=tokenizer.eos_token_id,
            )

        # Decodificar batch completo
        decoded = tokenizer.batch_decode(outputs, skip_special_tokens=True)
        unique_variants.update([s.replace(" ", "") for s in decoded])

    print(f"\nGeneración completada. Se obtuvieron {len(unique_variants)} variantes únicas.")
    return list(unique_variants)

In [ ]:
# ===================================================================
# EJEMPLO DE USO
# ===================================================================

# 1. Cargar el modelo y tokenizador afinados (si no están ya cargados)
model_path = "./models/prot_xlnet_finetuned"
tokenizer_fine_tuned = XLNetTokenizer.from_pretrained(str(output_dir))
model_fine_tuned = XLNetLMHeadModel.from_pretrained(str(output_dir))
model_fine_tuned.to(device)


# 2. Selecciona un subconjunto de tus mejores secuencias para usar como base
# (Recuerda que estas deben estar SIN espacios)
sequences_base = [
    "HAEGTFTSDVSSYLE*******GQKEFIAWLVKGR",
    "YAEGTFTSDYSIALEGQAAKEFIAWLVKGR",
    "HSQGTFTSDYSKYLDSRRAQDFVQWLMNT"
]

# 3. Llama a la función para generar las variantes
nuevas_variantes = generate_peptide_variants(
    prompt_sequences=sequences_base,
    model=model_fine_tuned,
    tokenizer=tokenizer_fine_tuned,
    num_variants_per_seq=10, # Pedimos 10 variantes por cada secuencia base
    min_length=28,
    max_length=40
)

# 4. Muestra los resultados
print("\n--- Primeras 15 variantes generadas ---")
for i, variant in enumerate(nuevas_variantes[:15]):
    print(f"{i+1}: {variant}")

c:\Users\Dev\.conda\envs\GLP1-Predict\Lib\site-packages\transformers\models\xlnet\configuration_xlnet.py:212: FutureWarning: The `use_cache` argument is deprecated and will be removed in a future version, use `use_mems_eval` instead.
  warnings.warn(


Iniciando generación de variantes para 3 secuencias base...


Procesando secuencias:   0%|          | 0/3 [00:00<?, ?it/s]


Generación completada. Se encontraron 30 variantes únicas.

--- Primeras 15 variantes generadas ---
1: HSQGTFTSDYSKYLDSRRAQDFVSWLMNT
2: HSQGTFTSDYSKELDSRRAQDFVQWLMNT
3: HAEGTFTSDVSSYLEGQAAKEWIAWLVKGR
4: YAEGTFTSDYSIALEGQAAKEFIAMLVKGR
5: HAEGTFTSDVSSYCEGQAAKEFIAWLVKGR
6: YAEGTFTSDYKIALEGQAAKEFIAWLVKGR
7: LAEGTFTSDVSSYLEGQAAKEFIAWLVKGR
8: HSQGTFTSDYSPYLDSRRAQDFVQWLMNT
9: YAEGTFTSDYSIAIEGQAAKEFIAWLVKGR
10: HAEGTFTSDVSSYLEGAAAKEFIAWLVKGR
11: HAEGTFTSDVSSYLEGQAAKFFIAWLVKGR
12: HSQGTFTSDYSKYLDSRRAQDFVQWCMNT
13: YAEGTFTSDYSIALEGQIAKEFIAWLVKGR
14: YAEGTFTSDYSIALEGQAAKEFRAWLVKGR
15: HAEGTFISDVSSYLEGQAAKEFIAWLVKGR


In [43]:
# ===================================================================
# EJEMPLO DE USO VARIANTE RÁPIDA
# ===================================================================

# 1. Cargar el modelo y tokenizador afinados (si no están ya cargados)
model_path = "./models/prot_xlnet_finetuned"
tokenizer_fine_tuned = XLNetTokenizer.from_pretrained(str(output_dir))
model_fine_tuned = XLNetLMHeadModel.from_pretrained(str(output_dir))
model_fine_tuned.to(device)


# 2. Selecciona un subconjunto de tus mejores secuencias para usar como base
# (Recuerda que estas deben estar SIN espacios)
sequences_base = [
 'HAEGTFTSDVSSYLEGQAAKEFIAWLVKR',
 'HADGTFTSDVSAYLKEQAIKDFVAKLKSGQ',
 'HSEGTFTSDFSSYLDYKATKEFIAQLTKGL',
 'HSEGTFTSDFSSYLEGKAAKEFIAWLVKGL',
 'HADGTFTSDMSSYLTDKAIRDFVARLKAGQ',
 'HSEGTFTNDVTRLLEEKATSEFIAWLLKGL',
]

# 3. Llama a la función para generar las variantes
nuevas_variantes = generate_peptide_variants_fast(
    prompt_sequences=sequences_base,
    model=model_fine_tuned,
    tokenizer=tokenizer_fine_tuned,
    num_variants_per_seq=10, # Pedimos 10 variantes por cada secuencia base
    min_length=28,
    max_length=40
)

# 4. Muestra los resultados
print("\n--- Primeras 15 variantes generadas ---")
for i, variant in enumerate(nuevas_variantes[:15]):
    print(f"{i+1}: {variant}")

Generando 60 variantes en lotes de 32...


Generando:   0%|          | 0/2 [00:00<?, ?it/s]

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.



Generación completada. Se obtuvieron 60 variantes únicas.

--- Primeras 15 variantes generadas ---
1: HSEGTFTDDFSSYLDYKATKEFIAQLTKGL
2: HSEGTFTNSVTRLLEEKATSEFIAWLLKGL
3: HSEGTFTSDFSSYLDYKATKEFCAQLTKGL
4: HAEGTFTYDVSSYLEGQAAKEFIAWLVKR
5: HADGTFTSDMSSYLTDKAIRDFVARLKDGQ
6: NAEGTFTSDVSSYLEGQAAKEFIAWLVKR
7: HSEGTFTNDVTRLGEEKATSEFIAWLLKGL
8: HADGTFTSDVSAYLKEQHIKDFVAKLKSGQ
9: HSEGTFTSDFSSYLDYKAIKEFIAQLTKGL
10: HSEGTFWSDFSSYLEGKAAKEFIAWLVKGL
11: HSEGTFTSDFSSYLEGKAAKEFIAWRVKGL
12: HSEGTFTIDFSSYLDYKATKEFIAQLTKGL
13: HADGTFWSDVSAYLKEQAIKDFVAKLKSGQ
14: HSEGTFTTDFSSYLEGKAAKEFIAWLVKGL
15: HADGTFTSDMSSYLTDKAIRDFVNRLKAGQ


In [44]:
!pip install -q transformers
!git clone https://github.com/jessevig/bertviz.git

Cloning into 'bertviz'...


In [50]:
model = XLNetModel.from_pretrained("Rostlab/prot_xlnet", output_attentions=True)
tokenizer = XLNetTokenizer.from_pretrained("Rostlab/prot_xlnet", do_lower_case=False)

In [55]:
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

In [56]:
model = model.to(device)
model = model.eval()

In [57]:
import torch
from transformers import XLNetTokenizer, XLNetModel
from bertviz.bertviz import head_view
import re

In [58]:
def show_head_view(model, tokenizer, sequence):
    inputs = tokenizer.encode_plus(sequence, return_tensors='pt', add_special_tokens=True)
    input_ids = inputs['input_ids']
    attention = model(input_ids.to(device))[-1]
    input_id_list = input_ids[0].tolist() # Batch index 0
    tokens = tokenizer.convert_ids_to_tokens(input_id_list)    
    head_view(attention, tokens)

In [59]:
def call_html():
  import IPython
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              "d3": "https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.8/d3.min",
              jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
            },
          });
        </script>
        '''))

In [61]:
call_html()
show_head_view(model, tokenizer, "B A E G T S D A K E F I W L V <sep> R")

<IPython.core.display.Javascript object>